In [44]:
import pandas as pd
import os
import torch
import json
import ast
import re
import warnings
import pandas as pd
warnings.filterwarnings('ignore')
os.environ['HF_HOME'] = '/raid/abhilash/huggingfacecache/huggingface/hub/'

from transformers import pipeline, AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig, AutoModel
from fuzzywuzzy import fuzz
from sentence_transformers import SentenceTransformer, util
from tqdm import tqdm
from transformers.utils import logging
logging.set_verbosity_error() 

In [3]:
NOTA_csv = 'reasoning_nota.csv'
df = pd.read_csv(NOTA_csv)

In [4]:
df

id          dataset  \
0      07d9bcf9-feb6-4d4a-858e-5570c5d9ef8b          medmcqa   
1      d8c969f3-fa33-421c-afb2-62f6fc51fa9b  medqa_taiwan_en   
2      8fe4e14c-4e17-4af0-94c2-0d8a59f342b8          medmcqa   
3      6bfcd1fd-e172-4490-bf96-5da1b8da7ed4          medmcqa   
4      dae6278f-b7f8-42ea-b5d6-3d76082df175          medmcqa   
...                                     ...              ...   
18861  a9c42f30-0265-4a86-9874-f4c869a4e37a  medqa_taiwan_en   
18862  5c963ea0-2dcc-4572-b58a-771456a3923e          medmcqa   
18863  681bc91c-034e-4bb9-860e-a2b1cbe29105          medmcqa   
18864  9c6c5c2d-432d-4f87-8a07-fc5621d2eaad        headqa_en   
18865  d80523f3-66c9-4abf-812a-5c100ee2dbbf          medmcqa   

                                                question  \
0                                    Zone 3 is known as:   
1      Which of the following potential sexual organ ...   
2                        Protein segregation occurs in ?   
3         What is the location of Meissner's corpuscles?   
4      Lacrimation is affected due to damage to which...   
...                                                  ...   
18861  Account of the major mechanisms of action of a...   
18862             Fomepizole is used in which poisoning?   
18863  To check objective pain response, which is bes...   
18864  The WPPSI IV is the Wechsler scale designed to...   
18865  Which of the following type of minor connector...   

                                                 options     correct_answer  \
0      {'0': 'Bacterial zone.', '1': 'Neutrophil rich...  None of the above   
1      {'0': 'Can self-breath test', '1': 'Dilated pu...  None of the above   
2      {'0': 'None of the above', '1': 'Peroxisomes',...  None of the above   
3      {'0': 'Lucidum', '1': 'Basale', '2': 'Reticula...  None of the above   
4      {'0': 'Nasociliary nerve', '1': 'None of the a...  None of the above   
...                                                  ...                ...   
18861  {'0': 'None of the above', '1': 'Fecal shell s...  None of the above   
18862  {'0': 'None of the above', '1': 'Benzodiazepin...  None of the above   
18863  {'0': 'None of the above', '1': 'Knee jerk ref...  None of the above   
18864  {'0': 'In the third age.', '1': 'In adults', '...  None of the above   
18865  {'0': 'Latticework construction', '1': 'Meshwo...  None of the above   

       correct_index split_type  subject_name topic_name    year  \
0                  2       test        Dental        NaN     NaN   
1                  2       test           NaN        NaN     NaN   
2                  0       test  Biochemistry        NaN     NaN   
3                  3        val       Anatomy       None     NaN   
4                  1        val       Anatomy       None     NaN   
...              ...        ...           ...        ...     ...   
18861              0       test           NaN        NaN     NaN   
18862              0       test       Unknown        NaN     NaN   
18863              0        val    Physiology       None     NaN   
18864              3       test    psychology        NaN  2017.0   
18865              2       test        Dental        NaN     NaN   

               exam_name  
0                    NaN  
1                    NaN  
2                    NaN  
3                    NaN  
4                    NaN  
...                  ...  
18861                NaN  
18862                NaN  
18863                NaN  
18864  Cuaderno_2017_1_P  
18865                NaN  

[18866 rows x 11 columns]

In [5]:
model_name = "BioMistral/BioMistral-7B"  # Specify the name or path of the Mistral model
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map="balanced_low_0",
    trust_remote_code=True,
    use_cache=False,
    revision="main",
    torch_dtype=torch.bfloat16,
    # load_in_8bit=True,
    cache_dir="/raid/abhilash/huggingfacecache/huggingface/hub/"
).half().eval()

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name, add_bos_token=True, trust_remote_code=True)

In [6]:
def generate(prompt):
    model_input = tokenizer(prompt, return_tensors="pt").to("cuda:"+str(3))
    output = model.generate(**model_input, max_new_tokens=200, repetition_penalty=1.15)
    answer = tokenizer.decode(output[0], skip_special_tokens=True)
    return answer

## DEFINE PROMPT TEMPLATES

In [8]:
few_shot_prompt_template = """As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'Temporo-mandibular ligament is attached to:', 'Options': {'0': 'Lateral aspect of TMJ', '1': 'Posterior aspect of TMJ', '2': 'Mandibular condyle', '3': 'Coronoid process'}}
Output: {'cop': 'Lateral aspect of TMJ', 'cop_index': 0, 'why_correct': 'The temporo-mandibular ligament is attached to the lateral aspect of the Temporo-Mandibular Joint (TMJ).', 'why_others_incorrect': 'The ligament is not attached to the posterior aspect of TMJ, the mandibular condyle, or the coronoid process.'}Stop Here

Input : {'Question': 'Parts of the brain that occur in epilepsy than aggressive behavior often appear?', 'Options': {'0': 'None of the above', '1': 'Parietal', '2': 'Occipital', '3': 'Basal ganglia'}}
Output: {'cop': 'None of the above', 'cop_index': 0, 'why_correct': 'No specific part of the brain is associated with aggression in epilepsy.', 'why_others_incorrect': 'The parietal, occipital, and basal ganglia are not specifically implicated in aggression in epilepsy.'}Stop Here
"""

zero_shot_prompt_template = """As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
"""

In [9]:
print(few_shot_prompt_template)

As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'Temporo-mandibular ligament is attached to:', 'Options': {'0': 'Lateral aspect of TMJ', '1': 'Posterior aspect of TMJ', '2': 'Mandibular condyle', '3': 'Coronoid process'}}
Output: {'cop': 'Lateral aspect of TMJ', 'cop_index': 0, 'why_correct': 'The temporo-mandibular ligament is attached to the lat

In [10]:
print(zero_shot_prompt_template)

As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}



## PREDICTION

In [11]:
def prepare_input(row, template="few_shot"):
    # d="Input: " + str({"Question": row['question'], "Options": eval(row['options'])}) + "\nOutput: "
    qstn=row['question']
    optn=row['options']
    d=f"Input: {{'Question': '{qstn}', 'Options': {optn}}}\nOutput: \n\n"
    if template=="zero_shot":
        d_ = zero_shot_prompt_template + "\n" + d
    else:
        d_ = few_shot_prompt_template + "\n" + d
    return d_

In [14]:
df.iloc[200, :]

id                             2d507d7c-d4e9-45ef-a6ed-2ffa49fd3162
dataset                                                     medmcqa
question                                    CSF rhinorrhea seen in:
options           {'0': 'Lefort 2 fracture.', '1': 'Lefort 3 fra...
correct_answer                                    None of the above
correct_index                                                     3
split_type                                                     test
subject_name                                                Surgery
topic_name                                                      NaN
year                                                            NaN
exam_name                                                       NaN
Name: 200, dtype: object

In [15]:
prompt=prepare_input(df.iloc[200, :])
print(generate(prompt))

As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'Temporo-mandibular ligament is attached to:', 'Options': {'0': 'Lateral aspect of TMJ', '1': 'Posterior aspect of TMJ', '2': 'Mandibular condyle', '3': 'Coronoid process'}}
Output: {'cop': 'Lateral aspect of TMJ', 'cop_index': 0, 'why_correct': 'The temporo-mandibular ligament is attached to the lat

In [23]:
final_preds = []
for ind, row in tqdm(df.iterrows()):
    print(ind)
    prompt = prepare_input(row)
    output = generate(prompt)
    final_preds.append(output)

0it [00:00, ?it/s]

0


1it [00:04,  4.84s/it]

1


2it [00:09,  4.66s/it]

...

18864it [33:37:54,  6.58s/it]

18864


18865it [33:37:59,  5.86s/it]

18865


18866it [33:38:09,  6.42s/it]


In [24]:
preds = pd.DataFrame(final_preds)
preds.to_csv('nota_predictions.csv', index=False)

In [32]:
print(preds.iloc[18668,0])

As a skilled medical domain expert, your role is to analyze multiple-choice questions, choose the correct answer from the given options, and provide a clear explanation for your choice. Additionally, you should explain why the other options are not correct. If none of the provided options is correct, choose 'none of the above'. Your explanation should be precise and free of incomplete or incorrect biomedical or clinical details.
Your output must be in the following JSON format: {'cop': 'correct option', 'cop_index' : 'index of correct option', 'why_correct': 'detailed explanation of correctness', 'why_others_incorrect': 'reasons other options are incorrect'}
Examples: 
Input : {'Question': 'Temporo-mandibular ligament is attached to:', 'Options': {'0': 'Lateral aspect of TMJ', '1': 'Posterior aspect of TMJ', '2': 'Mandibular condyle', '3': 'Coronoid process'}}
Output: {'cop': 'Lateral aspect of TMJ', 'cop_index': 0, 'why_correct': 'The temporo-mandibular ligament is attached to the lat

## EVALUATION

In [156]:
correct_score=1
incorrect_score=-0.25
fake_test_terms = ['none of the above', 'no idea', 'none of the option is correct', 'none', 'none is correct']

def calculate_score(correct, wrong):
    return (correct * correct_score + wrong * incorrect_score) / 100

def evaluate_answer(predicted, correct):
    if str(predicted.lower()) != str(correct.lower()):
        fuzzy_score = fuzz.ratio(predicted.lower(), correct.lower())/100.0
        emb1 = ss_model.encode(predicted.lower(), convert_to_tensor=True)
        emb2 = ss_model.encode(correct.lower(), convert_to_tensor=True)
        cosine_scores = util.pytorch_cos_sim(emb1, emb2)
        
        if (fuzzy_score+cosine_scores)/2 > 0/5:
            return True
        else:
            return False
    else:
        return True
    
def create_dataframe(task_name, correct, wrong, score):
    total = correct + wrong
    df_dict = {'task_name': [task_name], 'total': [total], 'correct': [correct], 'wrong': [wrong], 'score': [score]}
    return pd.DataFrame(df_dict)
    
def handle_exceptions(sample, exception):
    print(exception)
    return 1

num_to_text = {
    '0' : 'zero',
    '1' : 'one',
    '2' : 'two',
    '3' : 'three',
    '4' : 'four',
    '5' : 'five',
    '6' : 'six',
    '7' : 'seven',
    '8' : 'eight',
    '9' : 'nine'

}

def reasoning_nota_eval(pred, gt, gt_inds):
    correct = wrong = exception_count = 0
    
    for ind, pred in enumerate(tqdm(pred)):
        try:
            if pred['cop'] is not None:
                predicted_answer = pred['cop'].lower().strip()#str(sample['gpt_output']['cop']).lower()
            # predicted_reason = pred['why_correct'].lower()
            # cop_index = pred['cop_index'].lower()
            
                if any(len(set(term.split(' ')).intersection(predicted_answer.split(' ')))==min(len(term.split(' ')),len(predicted_answer.split(' '))) for term in fake_test_terms) or predicted_answer==gt.lower():
                    correct += 1
                    # print(f"ind {ind} :: {predicted_answer} == {gt}\n")
                    continue
                
                elif (str(predicted_answer) in str(gt_inds[ind])) or (str(predicted_answer) in num_to_text[str(gt_inds[ind])].lower()):
                    correct += 1
                    # print(f"ind {ind} :: {predicted_answer} == {gt_inds[ind]}\n")
                    continue
                    
            if (pred['cop_index'] is not None) and (str(pred['cop_index']) in str(gt_inds[ind])):
                correct += 1
                # print(f"ind {ind} :: {pred['cop_index']} == {gt_inds[ind]}\n")
                continue
            
            wrong += 1
            print(f"WRONG :: {pred['cop']} == {gt} \nWRONG :::::: {pred['cop_index']}=={gt_inds[ind]}")
            
        except Exception as e:
            print(f"Exception occured: {ind}")
            exception_count += handle_exceptions('NOTA', pred, e)

    print(f"correct {correct} wrong -> {wrong} exception_count {exception_count}")
    score = calculate_score(correct, wrong)  # calculate the score here
    return create_dataframe(task_name='Nota', correct=correct, wrong=wrong, score=score)

# def extract_values(string):
#     # Split the string on 'is_answer_correct'
#     parts = string.split("'is_answer_correct': '")
    
#     if len(parts) > 1:
#         # Extract the value of 'is_answer_correct'
#         is_answer_correct = parts[1].split("'")[0]
        
#         # Extract the value of 'correct_answer'
#         correct_answer = parts[1].split("'correct answer': '")[1].split("'")[0]
        
#         # Extract the value of 'why_correct'
#         why_correct = parts[1].split("'why_correct': '")[1].split("'")[0]
        
#         return is_answer_correct, correct_answer, why_correct
#     else:
#         return None, None, None
    
# def extract_values(string):
#     # Initialize variables with default values
#     cop = None
#     cop_index = None
#     why_correct = None
    
#     # Check if 'cop' is present in the string
#     if "'cop': '" in string:
#         cop = string.split("'cop': '")[1].split("'")[0]
    
#     # Check if 'cop_index' is present in the string
#     if "'cop_index': " in string:
#         cop_index = string.split("'cop_index': ")[1].split(",")[0]
    
#     # Check if 'why_correct' is present in the string
#     if "'why_correct': '" in string:
#         why_correct = string.split("'why_correct': '")[1].split("'")[0]
    
#     return cop, cop_index, why_correct

def extract_values(string):
    # Initialize variables with default values
    cop = None
    cop_index = None
    why_correct = None
    
    # string = string.replace("\'", "'")
    
    # Check if 'cop' is present in the string
    if "'cop': '" in string:
        start_index = string.find("'cop': '") + len("'cop': '")
        end_index = string.find("',", start_index)
        cop = string[start_index:end_index]
        
    # Check if 'cop_index' is present in the string
    if "'cop_index': " in string:
        cop_index = string.split("'cop_index': ")[1].split(",")[0]
    
    # Check if 'why_correct' is present in the string
    if "'why_correct': '" in string:
        start_index = string.find("'why_correct': '") + len("'why_correct': '")
        end_index = string.find("',", start_index)
        why_correct = string[start_index:end_index]
    
    return cop, cop_index, why_correct


# def extract_values(string):
#     cop_pattern = r"'cop':\s*'([^']*)'"
#     cop_index_pattern = r"'cop_index':\s*'([^']*)'"
    
#     why_correct_value = string.split("why_correct\':")[-1].strip().split("\'why_others_incorrect")[0].replace('\"', '')

#     cop_match = re.search(cop_pattern, string)
#     cop_index_match = re.search(cop_index_pattern, string)

#     cop_value = cop_match.group(1) if cop_match else None
#     cop_index_value = cop_index_match.group(1) if cop_index_match else None

#     return cop_value, cop_index_value, why_correct_value

In [20]:
'''
PREDICTIONS:::
get the predictions
'''
predictions = pd.read_csv('nota_predictions.csv')

In [25]:
'''
Ground-truth
'''
gt = pd.read_csv('reasoning_nota.csv')

In [27]:
gt.correct_answer.unique()

array(['None of the above'], dtype=object)

In [29]:
gt_ans = gt.correct_answer.unique()[0]
gt_ans

'None of the above'

In [95]:
'''
convert string outputs into dictionary
'''
pred_dict = []
for i, row in tqdm(predictions.iterrows()):
    model_out = row[0].split('Output:')[-1]
    cop, cop_index, why_correct = extract_values(model_out)
    pred_dict.append({'cop':cop, 'cop_index':cop_index, 'why_correct':why_correct})

18866it [00:01, 18047.99it/s]


In [157]:
'''
get accuracy and scores
'''
res_df = reasoning_nota_eval(pred_dict, gt_ans, gt.correct_index.tolist())

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 18866/18866 [00:00<00:00, 89242.32it/s]

WRONG :: Neutrophil rich zone. == None of the above 
WRONG :::::: 1==2
WRONG :: Meissner\'s corpuscles == None of the above 
WRONG :::::: 2==3
WRONG :: Trigeminal nerve == None of the above 
WRONG :::::: 2==1
WRONG :: Vimentin == None of the above 
WRONG :::::: 0==1
WRONG :: Rinses 0.2% NaF == None of the above 
WRONG :::::: 1==0
WRONG :: Sodium< Potassium == None of the above 
WRONG :::::: 0==3
WRONG :: Clot solubility test == None of the above 
WRONG :::::: 3==2
WRONG :: 3 hours == None of the above 
WRONG :::::: 3==0
WRONG :: Muscular tenderness with perispinal palpation == None of the above 
WRONG :::::: 1==3
WRONG :: Libman sacks == None of the above 
WRONG :::::: 0==1
WRONG :: 2 Walled defect == None of the above 
WRONG :::::: 1==0
WRONG :: Thoracodorsal nerve (Thoracodorsal nerve) == None of the above 
WRONG :::::: 1==0
WRONG :: Apo B-100. == None of the above 
WRONG :::::: 2==1
WRONG :: ①②③ == None of the above 
WRONG :::::: 0==2
WRONG :: The bottom wall of the eye socket (infe

In [158]:
res_df

task_name  total  correct  wrong    score
0      Nota  18866     9107   9759  66.6725

In [159]:
print(f"Accuracy = {(res_df['correct'][0]/res_df['total'][0])*100} \nScore = {res_df['score'][0]}")

Accuracy = 48.272023746422136 
Score = 66.6725
